In [1]:
import numpy as np
import scipy
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from func_util import *
from func_SE3_generators import *
from scipy.optimize import least_squares, minimize
from io import BytesIO
from PIL import Image

In [2]:
# Parse text file with calibration info
# Isometries bring a point from the camera ref. frame by left-multiply into robot frame of ref.
#lines = [float(line.rstrip('\n')) for line in open('/home/till/Testdata/Odometry/calib.txt')]
lines = [float(line.rstrip('\n')) for line in open('/tmp/calib.txt')]

nocams = int(lines[0])
#tr_l = []
#Rr_l = []
Pr_l = []
fc_l = []
cc_l = []
wh_l = []
i=1
for j in xrange(nocams):
    fc_l.append(np.array([lines[i], lines[i+1]]).astype(np.float32))
    cc_l.append(np.array([lines[i+2], lines[i+3]]).astype(np.float32))
    wh_l.append(np.array([lines[i+4], lines[i+5]]))
    i += 6    
    #tr = np.array([lines[i], lines[i+1], lines[i+2]]).astype(np.float32)
    #i += 3
    #Rr = np.array([[lines[i  ], lines[i+ 1], lines[i+ 2]],
    #                     [lines[i+ 3], lines[i+ 4], lines[i+ 5]],
    #                     [lines[i+ 6], lines[i+ 7], lines[i+ 8]]]).astype(np.float32)
    #i+=9
    #Pr_l.append(np.concatenate((Rr, tr[:,None]    ), axis=1)) 
    Pr_l.append(np.array(lines[i:(i+16)]).reshape((4,4)))
    i += 16
    #quat = func_dcm2quat(Pr_l[-1][0:3,0:3])
    #quat /= np.linalg.norm(quat)
    #Pr_l[-1][0:3,0:3] = func_quat2dcm(quat)
    #print Pr_l[-1]
    #print np.linalg.det(Pr_l[-1][0:3,0:3])
    

IndexError: list index out of range

In [ ]:
def func_invert_transform(Pin):
    P = Pin.copy()
    P[0:3,0:3] = P[0:3,0:3].T # R.T
    P[0:3,3] = np.dot(-P[0:3,0:3], P[0:3,3]) # -R.T * t
    return P

def func_P_to_Rt(P):
    return P[0:3,0:3], P[0:3,3]

# Display cameras in robot frame
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

for i in xrange(nocams):
    cc = cc_l[i] - wh_l[i]/2
    camcol = np.array([1.0, 0.0, 0.0])
    if (i==0):
        camcol = np.array([0.0, 0.0, 1.0])
    R,t = func_P_to_Rt(Pr_l[i])
    func_plot_cameras(ax, fc_l[i], cc, wh_l[i], R, t, rgbface=camcol, camerascaling=1)
    ax.scatter(0, 0, 0, color=camcol, linewidth=0.5)
    ax.scatter(t[0], t[1], t[2], color=camcol, linewidth=0.5)

func_set_axes_equal(ax)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
plt.show()


In [ ]:
# Parse vehicle pose file
# Isometries bring a point from vehicle frame to smooth frame
#lines = [float(line.rstrip('\n')) for line in open('/home/till/Testdata/Odometry/robotpose.txt')]    
lines = [float(line.rstrip('\n')) for line in open('/tmp/robotpose.txt')]    
noframes = len(lines)/16
#ts_l = []
#Rs_l = []
Ps_l = []
#print lines[0:12]
for j in xrange(noframes):
    #ts = np.array([lines[12*j], lines[12*j+1], lines[12*j+2]]).astype(np.float32)
    #Rs = np.array([[lines[12*j+ 3], lines[12*j+ 4], lines[12*j+ 5]],
    #                      [lines[12*j+ 6], lines[12*j+ 7], lines[12*j+ 8]],
    #                      [lines[12*j+ 9], lines[12*j+10], lines[12*j+11]]]).astype(np.float32)
    #Ps_l.append(np.concatenate((Rs, ts[:,None]    ), axis=1))   
    #Ps_l[-1] = np.row_stack((Ps_l[-1], np.array([0,0,0,1])))
    Ps_l.append(np.array(lines[(j*16):((j+1)*16)]).reshape((4,4)))
    

ts_np = np.stack([x[0:3,3] for x in Ps_l], axis=1)    

#def func_comb_vehicle_and_rig_pose(R_glob, t_glob, R_rig, t_rig):
#    R = np.dot(R_glob, R_rig)
#    t = np.dot(R_glob, t_rig) + t_glob   
#    return R,t
#
#def func_invert_transform(R,t):
#    return R.T, np.dot(-R.T,t)

def func_comb_vehicle_and_rig_pose(P_glob, P_rig):
    return np.dot(P_glob, P_rig)



In [ ]:
# Display cameras in smooth frame

fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
frmin=10
frmax=noframes-20
frstep=200
#frmin=11
#frmax=noframes-11
#frstep=1000
for fr in xrange(frmin,frmax,frstep):
    print fr
    for i in xrange(nocams):
        cc = cc_l[i] - wh_l[i]/2        
        camcol = np.array([1.0, 0.0, 0.0])        
        if (i==0):
            camcol = np.array([0.0, 0.0, 1.0])        
        #R,t = func_comb_vehicle_and_rig_pose(Rs_l[fr], ts_l[fr], Rr_l[i], tr_l[i])
        R,t = func_P_to_Rt(func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[i]))
        func_plot_cameras(ax, fc_l[i], cc, wh_l[i], R, t, rgbface=camcol, camerascaling=1)
        
    ax.scatter(ts_np[0,fr],ts_np[1,fr],ts_np[2,fr], color=np.array([0.0, 0.0, 0.0]), linewidth=5)
    ax.text(ts_np[0,fr],ts_np[1,fr],ts_np[2,fr]-5, str(fr))

ax.plot(ts_np[0,(frmin-10):(frmax+10)],ts_np[1,(frmin-10):(frmax+10)],ts_np[2,(frmin-10):(frmax+10)], color=np.array([0.0, 0.0, 0.0]), linewidth=0.5)

func_set_axes_equal(ax)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
plt.show()

In [ ]:

# Minimize camera pose (directly, NOT through baselink) error on reprojection error
fr = 30
camno = 0
#R, t = func_comb_vehicle_and_rig_pose(Rs_l[fr], ts_l[fr], Rr_l[camno], tr_l[camno])
P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
R,t = func_P_to_Rt(P)

fc = fc_l[camno]
wh = wh_l[camno]
cc = cc_l[camno] - wh/2
#Rinv, tinv = func_invert_transform(R,t) # use inverse transform for reprojections
Pinv = func_invert_transform(P)
Rinv,tinv = func_P_to_Rt(Pinv)

#Rinv2, tinv2 = func_invert_transform(Rinv,tinv)
Rinv2,tinv2 = func_P_to_Rt(func_invert_transform(Pinv))
assert(np.linalg.norm(R - Rinv2) < 1e-3)
assert(np.linalg.norm(t - tinv2) < 1e-3)


# Generate points, reproject into GT camera
nopts = 6
pt3d = 4*np.random.rand(nopts,3)-2.0
pt3d += (R[:,2] * 6) + t
pt2dGT = func_reproject(pt3d, Rinv, tinv, fc, cc)

def comp_residual(Pin):
    res = pt2dGT - func_reproject(pt3d, Pin[0:3,0:3], Pin[0:3,3], fc, cc)
    return res.T.reshape(-1) # order: all [all X residuals, all Y residuals]
    #print np.mean(comp_residual(R, t)**2)

def comp_residual_SE3_coeff(coeffiter):
    isom = func_SE3_coefficients_to_Group(coeffiter)
    #return comp_residual(isom[0:3,0:3], isom[0:3,3])
    return comp_residual(isom)


# Perturb camera. We use fr-5 as starting frame
frstart = fr-5
#Rinit, tinit = func_comb_vehicle_and_rig_pose(Rs_l[frstart], ts_l[frstart], Rr_l[camno], tr_l[camno])
#Rinitinv, tinitinv = func_invert_transform(Rinit,tinit)
Pinit = func_comb_vehicle_and_rig_pose(Ps_l[frstart], Pr_l[camno])
Rinit,tinit = func_P_to_Rt(Pinit)
Pinitinv = func_invert_transform(Pinit).astype(np.float64)
Rinitinv,tinitinv = func_P_to_Rt(Pinitinv)
#G = np.zeros((4,4), dtype=np.float64)    
#G[0:3,0:3] = Rinitinv
#G[0:3,3] = tinitinv
#G[3,3] = 1

# Optimize with Scipy
x0 = func_SE3_Group_to_coefficients(Pinitinv)
xsolvinv = least_squares(comp_residual_SE3_coeff, x0, verbose=1, method='lm') 
Psolvinv = func_SE3_coefficients_to_Group(xsolvinv.x)
#Rsolvinv = Psolvinv[0:3,0:3]
#tsolvinv = Psolvinv[0:3,3]
#Rsolv,tsolv = func_invert_transform(Rsolvinv,tsolvinv)
Rsolv,tsolv = func_P_to_Rt(func_invert_transform(Psolvinv))

print "Init pos. error: ", np.linalg.norm(tinit-t), "meters, final error: ", np.linalg.norm(tsolv - t), "meters"


# Display camera and points
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
func_plot_cameras(ax, fc, cc , wh, R, t, rgbface=np.array([1.0, 0.0, 0.0]), camerascaling=1)
func_plot_cameras(ax, fc, cc , wh, Rinit, tinit, rgbface=np.array([0.0, 0.0, 1.0]), camerascaling=1)
func_plot_cameras(ax, fc, cc , wh, Rsolv, tsolv, rgbface=np.array([0.0, 1.0, 0.0]), camerascaling=1)
ax.scatter(pt3d[:,0],pt3d[:,1],pt3d[:,2], color=np.array([0.0, 0.0, 0.0]), linewidth=5)
ax.scatter(ts_np[0,fr],ts_np[1,fr],ts_np[2,fr], color=np.array([0.0, 0.0, 0.0]), linewidth=5)
ax.plot(ts_np[0,(fr-10):(fr+10)],ts_np[1,(fr-10):(fr+10)],ts_np[2,(fr-10):(fr+10)], color=np.array([0.0, 0.0, 0.0]), linewidth=0.5)
func_set_axes_equal(ax)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
plt.show()

# Display: 2D point reprojection, corresponding points in blue/red overlaid in same image
plt.figure()
plt.scatter(pt2dGT[:,0]+wh[0]/2, pt2dGT[:,1]+wh[1]/2, 5, color='blue')
#plt.scatter(pts_GT2D_r[:,0], pts_GT2D_r[:,1], 5, color='blue')
plt.axis('image')
plt.axis([0, wh[0], wh[1], 0])
plt.title('Blue: GT, Red: reprojection at current estimate.')
plt.show()
plt.figure()




In [ ]:
# Do same thing with jacobian with auto differentiation
def comp_jac_autodiff(x):
    repo0 = comp_residual_SE3_coeff(x)
    jac_l = []
    deltap = 1e-10
    for i in xrange(len(x)):
        xhere = x.copy()
        xhere[i] += deltap
        jac_l.append((comp_residual_SE3_coeff(xhere) - repo0)/deltap)
    jac = np.stack(jac_l, axis=1)
    return jac

# Optimize with Scipy
x0 = func_SE3_Group_to_coefficients(Pinitinv)
xsolvinv = least_squares(comp_residual_SE3_coeff, x0, jac=comp_jac_autodiff, verbose=1, method='lm') 
Psolvinv = func_SE3_coefficients_to_Group(xsolvinv.x)
Rsolv,tsolv = func_P_to_Rt(func_invert_transform(Psolvinv))
print "Init pos. error: ", np.linalg.norm(tinit-t), "meters, final error: ", np.linalg.norm(tsolv - t), "meters"
#print comp_jac_autodiff(x0).astype(int)
#print xsolv.jac.astype(int)

In [ ]:
# Minimize camera pose (INDIRECTLY through baselink, fixed camera rig) error on reprojection error

def comp_residual_SE3_coeff_rig(coeffiter):
    isom = func_SE3_coefficients_to_Group(coeffiter)
    Pinv = func_invert_transform(func_comb_vehicle_and_rig_pose(isom, Pr_l[camno]))    
    return comp_residual(Pinv)

def comp_jac_autodiff_rig(x): # use pose directly, NOT inverse global pose
    repo0 = comp_residual_SE3_coeff_rig(x)
    jac_l = []
    deltap = 1e-10
    for i in xrange(len(x)):
        xhere = x.copy()
        xhere[i] += deltap
        jac_l.append((comp_residual_SE3_coeff_rig(xhere)-repo0)/deltap)
    jac = np.stack(jac_l, axis=1)
    return jac

#GT
R,t = func_P_to_Rt(Ps_l[fr])

# Perturb camera. We use fr-5 as starting frame
frstart = fr-5
Pinit = Ps_l[frstart]
Rinit,tinit = func_P_to_Rt(Pinit)

# Optimize with Scipy
x0 = func_SE3_Group_to_coefficients(Pinit)
xsolv = least_squares(comp_residual_SE3_coeff_rig, x0, jac=comp_jac_autodiff_rig, verbose=1, method='lm') 
Psolv = func_SE3_coefficients_to_Group(xsolv.x)
Rsolv,tsolv = func_P_to_Rt(Psolv)
print "Init pos. error: ", np.linalg.norm(tinit-t), "meters, final error: ", np.linalg.norm(tsolv - t), "meters"


In [ ]:
# Triangulation test

def func_pt_triangulate_from_P_linear_sq_DLT(P_l, xin_l):
    nocams = len(xin_l)
    A = np.zeros((2*nocams,4), dtype=float)
    for i in xrange(nocams):
        P = P_l[i].copy()
        x = xin_l[i].copy()
        H = np.array([[2.0/wh[0], 0, -1,0], [0, 2/wh[1], -1,0], [0,0, 1,0], [0,0,0,1]])
        P = np.dot(H, P)
        x[0] = 2.0/wh[0]*x[0] - 1.0
        x[1] = 2.0/wh[1]*x[1] - 1.0
        
        A[2*i  , :] = x[0]*P[2,:] - P[0,:]
        A[2*i+1, :] = x[1]*P[2,:] - P[1,:]
        
    # Assume uncorrelated observation noise
    XtX = np.linalg.inv(np.dot(A[:,0:3].T,A[:,0:3])) # Use this as covariance estimate at solution    

    return np.dot(np.dot(XtX, A[:,0:3].T), -A[:,3])  # Solves (X`T X)^-1 X`T y


frstart = 0
camno = 0
P = func_comb_vehicle_and_rig_pose(Ps_l[frstart], Pr_l[camno])
R,t = func_P_to_Rt(P)

fc = fc_l[camno]
wh = wh_l[camno]
cc = cc_l[camno]

K = np.identity(4)
K[0,0] = fc[0]
K[1,1] = fc[1]
K[0,2] = cc[0]
K[1,2] = cc[1]
    
Pinv = func_invert_transform(P)
Rinv,tinv = func_P_to_Rt(Pinv)

# Generate points, reproject into GT camera
nopts = 1
pt3d = 5*np.random.rand(nopts,3)-2.5
pt3d += (R[:,2] * 10) + t

xdlt_l = []
Pinvdlt_l = []
frend = frstart + 5
for fr in xrange(frend-1, frstart-1, -1):
    P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
    Pinv = func_invert_transform(P)
    R,t = func_P_to_Rt(P)
    Rinv,tinv = func_P_to_Rt(Pinv)
    xdlt_l.append(func_reproject(pt3d, Rinv, tinv, fc, cc)[0,:])
    
    #print func_reproject(pt3d, Rinv, tinv, fc, cc)[0,:]
    #a = np.dot(np.dot(K, Pinv), np.array([pt3d[0,0], pt3d[0,1], pt3d[0,2],1]))
    #a = np.array([a[0]/a[2], a[1]/a[2]])
    #print a
    
    Pinvdlt_l.append(np.dot(K, Pinv))
    #print Pinvdlt_l[-1]
print len(xdlt_l)

pt3d_res =  func_pt_triangulate_from_P_linear_sq_DLT(Pinvdlt_l, xdlt_l)
print pt3d, pt3d_res
print np.linalg.norm(pt3d - pt3d_res)

fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
for fr in xrange(frend-1, frstart-1, -1):
    P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
    R,t = func_P_to_Rt(P)
    func_plot_cameras(ax, fc, cc-wh/2 , wh, R, t, rgbface=np.array([1.0, 0.0, 0.0]), camerascaling=1)

ax.scatter(pt3d[:,0],pt3d[:,1],pt3d[:,2], color=np.array([0.0, 0.0, 0.0]), linewidth=5)
#ax.scatter(pt3d_res[0],pt3d_res[1],pt3d_res[2], color=np.array([0.0, 0.0, 1.0]), linewidth=5)

func_set_axes_equal(ax)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
plt.show()

#print np.row_stack(xdlt_l)
for fr,i in zip(xrange(frend-1, frstart-1, -1), xrange(len(xdlt_l))):
    P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
    Rinv,tinv = func_P_to_Rt(func_invert_transform(P))
    print xdlt_l[i]-func_reproject(np.array(pt3d_res)[None,:], Rinv, tinv, fc, cc)[0,:]    


In [ ]:
# Display 
full3Dcov = False
nstd = 3

np.random.seed(23)

outpath = '/tmp/'
rndcol = []
for camno in xrange(nocams):
    rndcol.append(np.random.rand(3))
    
for fr in xrange(49,noframes):
    fig = plt.figure(figsize=(18,14))
    ax = fig.add_subplot(111, projection='3d')
    ax.hold('on')
    for camno in [0]:#,1]:#,4,5,6,7,8,9]:#xrange(2):#nocams):
        P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
        R,t = func_P_to_Rt(P)

        #col = rndcol[camno]
        col = np.array([1.0, 0.0, 0.0])
        func_plot_cameras(ax, fc, cc-wh/2 , wh, R, t, rgbface=col, camerascaling=1)

        lines = [float(line.rstrip('\n')) for line in open("/tmp/pts_cam{:02d}_{:06d}.txt".format(camno, fr))]
        if (len(lines)>0):
            ptstmp = np.split(np.array(lines), len(lines)/15)

            pt3d = [x[0:3] for x in ptstmp]
            pt3d = np.row_stack(pt3d)

            pt3d_col = [x[3:6] for x in ptstmp]
            pt3d_col = np.row_stack(pt3d_col)/255.0

            pt3d_cov = [x[6::].reshape(3,3)[:,:,None] for x in ptstmp]
            pt3d_cov = np.concatenate(pt3d_cov, axis=2)

            covdet = np.array([np.linalg.det(pt3d_cov[:,:,ll]) for ll in xrange(pt3d_cov.shape[2])])
            #idxkeep = np.where(covdet<1e-9)[0]
            idxkeep = np.where(covdet<1e9)[0]
                    
            ax.scatter(pt3d[idxkeep,0],pt3d[idxkeep,1],pt3d[idxkeep,2], color=col, linewidth=.01)
            for ll in idxkeep:
                #col = pt3d_col[ll,:]
                #ax.scatter(pt3d[ll,0],pt3d[ll,1],pt3d[ll,2], color=col, linewidth=.01)
                if (full3Dcov):
                    ell = func_get_cov_ellipsoid(pt3d_cov[:,:,ll], Nstd=nstd, nobins=20) + pt3d[ll,:][:,None,None]
                    ax.plot_surface(ell[0,:], ell[1,:], ell[2,:],  rstride=4, cstride=4, color=col, alpha=0.1, linewidth=0, antialiased=False)
                else:
                    depthvar = pt3d_cov[0,0,ll]
                    depthsig = nstd*np.sqrt(depthvar)
                    ptdir = t-pt3d[ll,:]
                    ptdir = ptdir / np.linalg.norm(ptdir)
                    ax.plot([pt3d[ll,0] - depthsig*ptdir[0],pt3d[ll,0] + depthsig*ptdir[0]],
                            [pt3d[ll,1] - depthsig*ptdir[1],pt3d[ll,1] + depthsig*ptdir[1]],
                            [pt3d[ll,2] - depthsig*ptdir[2],pt3d[ll,2] + depthsig*ptdir[2]], color=col, alpha=0.1)

    # plot retired points
    col = np.array([0.0, 0.0, 1.0])
    lines = [float(line.rstrip('\n')) for line in open("/tmp/pts_cam{:02d}_{:06d}_retired.txt".format(camno, fr))]
    if (len(lines)>0):
        ptstmp = np.split(np.array(lines), len(lines)/12)
        pt3d = [x[0:3] for x in ptstmp]
        pt3d = np.row_stack(pt3d)
        pt3d_cov = [x[3::].reshape(3,3)[:,:,None] for x in ptstmp]
        pt3d_cov = np.concatenate(pt3d_cov, axis=2)
        covdet = np.array([np.linalg.det(pt3d_cov[:,:,ll]) for ll in xrange(pt3d_cov.shape[2])])
        #idxkeep = np.where(covdet<1e-9)[0]
        idxkeep = np.where(covdet<1e9)[0]

        
        ax.scatter(pt3d[idxkeep,0],pt3d[idxkeep,1],pt3d[idxkeep,2], color=col, linewidth=.01)
        for ll in idxkeep:
            #col = pt3d_col[ll,:]
            #ax.scatter(pt3d[ll,0],pt3d[ll,1],pt3d[ll,2], color=col, linewidth=.01)
            if (full3Dcov):
                ell = func_get_cov_ellipsoid(pt3d_cov[:,:,ll], Nstd=nstd, nobins=20) + pt3d[ll,:][:,None,None]
                ax.plot_surface(ell[0,:], ell[1,:], ell[2,:],  rstride=4, cstride=4, color=col, alpha=0.1, linewidth=0, antialiased=False)
            else:
                depthvar = pt3d_cov[0,0,ll]
                depthsig = nstd*np.sqrt(depthvar)
                ptdir = t-pt3d[ll,:]
                ptdir = ptdir / np.linalg.norm(ptdir)
                ax.plot([pt3d[ll,0] - depthsig*ptdir[0],pt3d[ll,0] + depthsig*ptdir[0]],
                        [pt3d[ll,1] - depthsig*ptdir[1],pt3d[ll,1] + depthsig*ptdir[1]],
                        [pt3d[ll,2] - depthsig*ptdir[2],pt3d[ll,2] + depthsig*ptdir[2]], color=col, alpha=0.1)

            
    ax.scatter(ts_np[0,fr],ts_np[1,fr],ts_np[2,fr], color=np.array([0.0, 0.0, 0.0]), linewidth=5)
    ax.plot(ts_np[0,0:fr],ts_np[1,0:fr],ts_np[2,0:fr], color=np.array([0.0, 0.0, 0.0]), linewidth=0.5)

    R,t_glob = func_P_to_Rt(Ps_l[fr])

    ax.set_xlim(t_glob[0]-25, t_glob[0]+25)
    ax.set_ylim(t_glob[1]-25, t_glob[1]+25)
    ax.set_zlim(t_glob[2]-4.5, t_glob[2]+4.5)    
    #ax.view_init(elev=90., azim=1.0)    
    func_set_axes_equal(ax)
    plt.show()

    savefile =  outpath + "vis_plot_triang3D_{:06d}.png".format(fr)
    fig.savefig(savefile, format='png')
    #png2 = Image.open(png1)
    #png2.save(savefile)



In [ ]:
# Display 
fr = 10
camno = 2

lines = [float(line.rstrip('\n')) for line in open("/tmp/pts_cam{:02d}_{:06d}.txt".format(camno, fr))]
tracktmp = np.split(np.array(lines), len(lines)/120)
tracktmp = [x.reshape((60,2)) for x in tracktmp]

res_total_l = []
pt3d_res_l = []

tracktmp_reproj = []
for l in xrange(len(tracktmp)):
    xdlt_l = np.split(tracktmp[l], 60, axis=0)
    xdlt_l = [x[0,:] for x in xdlt_l]
    xdlt_reproj_l = []
    pt3d_res =  func_pt_triangulate_from_P_linear_sq_DLT(Pinvdlt_l, xdlt_l)
    pt3d_res_l.append(pt3d_res)
    #print pt3d_res

    residual_total = 0
    for fr,i in zip(xrange(frend-1, frstart-1, -1), xrange(len(xdlt_l))):
        P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
        Rinv,tinv = func_P_to_Rt(func_invert_transform(P))
        xdlt_reproj_l.append(func_reproject(np.array(pt3d_res)[None,:], Rinv, tinv, fc, cc)[0,:])
        residual = xdlt_l[i] - xdlt_reproj_l[-1]
        residual_total += np.sum(residual**2)
    #print residual_total
    res_total_l.append(np.sqrt(residual_total/len(xdlt_l)))
    
    tracktmp_reproj.append(xdlt_reproj_l)

pt3d_res = np.row_stack(pt3d_res_l)

print "rmsq triangulation error", np.mean(np.array(res_total_l))

fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
for fr in xrange(frend-1, frstart-1, -1):
    P = func_comb_vehicle_and_rig_pose(Ps_l[fr], Pr_l[camno])
    R,t = func_P_to_Rt(P)
    func_plot_cameras(ax, fc, cc-wh/2 , wh, R, t, rgbface=np.array([1.0, 0.0, 0.0]), camerascaling=1)

ax.scatter(pt3d_res[:,0],pt3d_res[:,1],pt3d_res[:,2], color=np.array([0.0, 0.0, 1.0]), linewidth=5)

func_set_axes_equal(ax)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
plt.show()


for fr,i in zip(xrange(frend-1, frstart, - 1), xrange(len(xdlt_l))):
    plt.figure(figsize=(16,10))
    for l in xrange(len(tracktmp_reproj)):#len(tracktmp)):
        pt2dtrack = tracktmp[l][[i, i+1],:]
        #print pt2dtrack.shape
        pt2dreproj = tracktmp_reproj[l][i]
        plt.scatter(pt2dreproj[0], pt2dreproj[1], 5, color='blue')
        plt.plot(pt2dtrack[:,0], pt2dtrack[:,1], "-", color='red')
    plt.axis('image')
    plt.axis([0, wh[0], wh[1], 0])
    plt.savefig('/home/till/Downloads/{}.png'.format(fr))
    plt.show()
    plt.figure()


In [ ]:
import cv2
ppath = '/home/till/Results/DepthUncertainty/'
offset = 2000
for fr in xrange(1,2500):
    print fr
    img = cv2.imread(ppath + "vis_plot_triang3D_{:06d}.png".format(fr))
    imga = cv2.imread("/home/till/Results/out_west_wide_right_{:06d}.png".format(fr+offset))
    imgb = cv2.imread("/home/till/Results/out_north_wide_left_{:06d}.png".format(fr+offset))
    imgc = cv2.imread("/home/till/Results/out_north_wide_right_{:06d}.png".format(fr+offset))
    imgd = cv2.imread("/home/till/Results/out_east_wide_left_{:06d}.png".format(fr+offset))
    w = img.shape[1]/4
    h = img.shape[0]/4
    img[-h:, 0:w,:] = cv2.resize(imga, (w, h))
    img[-h:, w:(2*w),:] = cv2.resize(imgb, (w, h))
    img[-h:, (2*w):(3*w),:] = cv2.resize(imgc, (w, h))
    img[-h:, (3*w):(4*w),:] = cv2.resize(imgd, (w, h))
    cv2.imwrite(ppath + "visimg_plot_triang3D_{:06d}.png".format(fr), img)
